In [9]:
#Change: save top 5 correlated images

%matplotlib notebook

from datetime import datetime, timedelta
#import quandl
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from matplotlib import style
from pylab import figure, axes, pie, title, show
style.use('fivethirtyeight')

#for creating directories
import os

#api_key = 'kgMN5tuNUwb7-F29s6xp' 

##----------TRAINING DATA
main_df = pd.DataFrame()

file = '1min_training.csv'
df = pd.read_csv('data/training_data/'+file)
df = df.set_index('Index').T

for column in df:    
    main_df[column] = (df[column] - df[column].iloc[0]) / df[column].iloc[0] * 100

#CURRENT
df2= main_df
df3 = pd.DataFrame()
main_df3 = pd.DataFrame()
stock_open = pd.DataFrame()
df_corr_results = pd.DataFrame()
main_df_corr_results = pd.DataFrame()
main_plot = pd.DataFrame()

#---------THE FILES TO ANALYZE
#df3 = pd.read_csv('gainers-loser/daily_exports/file 4-2017.csv')
test_file = '1min_test_temp.csv'
test1 = pd.read_csv('data/daily_exports/'+test_file)
#test1 = pd.read_csv('data/daily_exports/gainers_2017-05-24-25-26.csv')
test1 = test1.set_index('Index').T

# create dictionary that contains first value for each stock
# https://www.reddit.com/r/learnpython/comments/68cad0/pandas_iterate_over_columns/
for column in df.columns:
    header = format(column)
    value = df[header].iloc[0]
    stock_open[header] = [ value ]
    #print(header)
    #print(df[header].iloc[0])

def corr_data(stock_num,corr_calc_value,df2,test1,stock_open):


    #-------main training data
    df3 = test1
    for column in df3:    
        main_df3[column] = (df3[column] - df3[column].iloc[0]) / df3[column].iloc[0] * 100

    analyze_stock_text = df3.columns.values[stock_num]
    x1 = main_df3[analyze_stock_text] # convert selected stock to series so you can coorilate
    analyze_plots = pd.DataFrame(data=main_df3[analyze_stock_text]) #convert into df to use to plot

    #below was for testing when future is needed
    # analyze_plots = pd.DataFrame(data=main_df3[analyze_stock_text][:num_days]) #convert into df to use to plot
    # num_days = num_days - 1 #reset line start to match with current line
    # analyze_plots_future = pd.DataFrame(data=main_df3[analyze_stock_text][num_days:]) # Get future results
    #---------pick a stock

    # correlate selected stock to all test data stocks
    df_corr_results = df2.corrwith(x1)
    main_df_corr_results = df_corr_results.sort_values(ascending=False)
    main_df_corr_results = pd.DataFrame({'Stock':main_df_corr_results.index, 'Corr':main_df_corr_results.values}) #turns series into a dataframe

    d = datetime.today() - timedelta(days=1) # today's day  minus one for plot display

    first_loop = 0 #FOR TELLING IF THERE ARE ANY STOCKS TO ANALYZE

    for index, row in main_df_corr_results.iterrows(): # loop each value of main_df_corr...

        if row['Corr'] >= corr_calc_value:
            
            # adjust plot titles
            #bench
            #train_open = open_df2['DMPI']
            train_open = stock_open[ row['Stock'] ].iloc[0]
            benchmark_stock_text = row['Stock']
            bench_date, bench_stock = benchmark_stock_text.split('|')
            date_object = datetime.strptime(bench_date, '%Y-%m-%d')
            bench_date = date_object.strftime('%d-%b-%y')
            title_benchmark_stock_text = bench_stock+'|'+bench_date+'|'+str(train_open)
            
            #other
            test_open = df3[column].iloc[0]
            analy_date, analy_stock = analyze_stock_text.split('|')
            date_object = datetime.strptime(analy_date, '%Y-%m-%d')
            analy_date = date_object.strftime('%d-%b-%y')
            title_analyze_stock_text = analy_stock+'|'+analy_date+'|'+str(test_open)
            
            

            #show correlated values
            print('TEST: '+str(analyze_stock_text))
            print (row['Corr'], row['Stock'])
            print()

            #---------pick a benchmark
            print('Train: '+str(benchmark_stock_text))
            benchmark_plots = pd.DataFrame(data=df2[benchmark_stock_text]) #loopup benchmark data using TEXT
            #---------pick a benchmark

            # plot data
            main_plot['Train: '+title_benchmark_stock_text] = benchmark_plots[benchmark_stock_text]
            main_plot[''+title_analyze_stock_text] = analyze_plots[analyze_stock_text]
            #main_plot['Future:'+analyze_stock_text] = analyze_plots_future # uncomment for future
            main_plot.plot()
            corr = int(row['Corr'] * 100)
            plt.title('Corr='+ str(corr)+'%')
            plt.xlabel('['+str(stock_num)+'] '+file+'\nLast Stock Update: '+d.strftime('%Y-%m-%d'), fontsize=10)
            plt.tight_layout() # make room for lables
            
            #-----------save file
            #make directory to today's files
            path = str(date_object.date()) #show just the date...drop 00:00:00
            try: 
                os.makedirs(path)
            except OSError:
                if not os.path.isdir(path):
                    raise
            plt.savefig(path+'/'+analy_stock+'-'+str(first_loop)+'.png', bbox_inches='tight')
            
            #show graph on this page
            plt.show() # you can also use plt.show()

            del main_plot['Train: '+title_benchmark_stock_text] # delete line from PLOT
            del main_plot[title_analyze_stock_text]
            #del main_plot['Future:'+analyze_stock_text] # uncomment for future
            
            #only show first 5 correlated files
            first_loop = first_loop + 1
            if first_loop == 5:
                break;
            
        else: # if row['Corr'] >= .80
            if first_loop == 0:
                print('NO STOCKS TO ANALYZE')
            break

corr_data(0,.1,df2,test1,stock_open)

# # #count all lines of test1
# loop_times = len(test1.columns)

# for stock in range(loop_times):
#     # stock position to analyze, correlation % 
#     corr_data(stock,.1,df2,test1,stock_open,path)
            


AttributeError: 'DataFrame' object has no attribute 'tolist'